# White Dwarfs

In [ ]:

using OrdinaryDiffEqTsit5
using PyPlot

In [ ]:

function white_dwarf_eqs!(dudr, u, p, r)
    m = u[1]
    rho = u[2]
    rho_c = p
    if rho >= 0.0
        w = rho^(2/3)
        gamma = w/(3 * sqrt(1 + w))
        dudr[1] = r^2 * rho
        if r > 1e-6
            dudr[2] = - m * rho / (gamma *r^2)
        else
            dudr[2] = - rho_c/3 * r * rho / gamma
        end
    else
        dudr[1] = 0.0
        dudr[2] = 0.0
    end
    return nothing
end

In [ ]:

np = 100
rho_c1 = 0.08
rho_c2 = 100000.0

rhos = exp.(range(log(rho_c1), log(rho_c2), np));

In [ ]:

radi = zeros(np)
mass = zeros(np);

In [ ]:

rspan = (0.0, 10.0)
for i = 1:np
    rho_c = rhos[i]
    u0 = [0.0, rho_c]
    prob = ODEProblem(white_dwarf_eqs!, u0, rspan, rho_c)
    
    condition(u, t, integrator) = u[2]
    affect!(integrator) = terminate!(integrator)
    cb = ContinuousCallback(condition, affect!)

    sol = solve(prob, Tsit5(), callback=cb)

    radi[i] = sol.t[end]
    mass[i] = sol(radi[i])[1]
end

In [ ]:
plot(mass, radi)

In [ ]:

using DataFrames
using CSV

In [ ]:

url = "http://vizier.u-strasbg.fr/viz-bin/asu-tsv?-source=J/A+A/420/507/tablea1&-out=Mass&-out=Rad"
catalog = download(url)
df = CSV.read(catalog, DataFrame, comment="#", skipto=4, 
              types=[Float64, Float64], delim='\t', ignorerepeated=true, 
              silencewarnings=true)
dropmissing!(df);

In [ ]:

# The constants convert our dimensionless units to the units of the solar mass and solar radius
plot(mass*0.71, radi*0.006, label="theory") 
plot(df.Mass, df.Rad, marker="o", linestyle="none", 
     fillstyle="none", markersize=4, label="observations")
grid(true)
xlabel(L"$M/M_{\odot}$")
ylabel(L"$R/R_{\odot}$")
legend();